In [1]:
import tensorflow as tf
import numpy as np
import math
import time
import random
from collections import defaultdict
from tensorflow.keras import layers

In [2]:
# The length of the n-gram
N = 2 # The length of the n-gram
EMB_SIZE = 128 # The size of the embedding
HID_SIZE = 128 # The size of the hidden layer


# Functions to read in the corpus
# NOTE: We are using data from the Penn Treebank, which is already converted
#       into an easy-to-use format with "<unk>" symbols. If we were using other
#       data we would have to do pre-processing and consider how to choose
#       unknown words, etc.
w2i = defaultdict(lambda: len(w2i))
S = w2i["<s>"]
UNK = w2i["<unk>"]
def read_dataset(filename):
    with open(filename, "r") as f:
        for line in f:
            yield [w2i[x] for x in line.strip().split(" ")]

In [3]:
# Read in the data
train = list(read_dataset("../data/ptb/train.txt"))
w2i = defaultdict(lambda: UNK, w2i)
dev = list(read_dataset("../data/ptb/valid.txt"))
i2w = {v: k for k, v in w2i.items()}
nwords = len(w2i)

In [4]:
class FFN_LM(tf.keras.Model):
    def __init__(self, nwords, emb_size, hid_size, num_hist, dropout):
        super(FFN_LM, self).__init__()
        self.embedding = layers.Embedding(nwords, emb_size)
        self.fnn = tf.keras.Sequential()
        self.fnn.add(layers.Dense(hid_size, activation='tanh'))
        self.fnn.add(layers.Dropout(dropout))
        self.fnn.add(layers.Dense(nwords))

    def call(self, inputs):
        # 3D Tensor of size [batch_size x num_hist x emb_size]
        emb_out = self.embedding(inputs) 
        # 2D Tensor of size [batch_size x (num_hist * emb_size)]
        emb_view =  tf.reshape(emb_out, [tf.shape(emb_out)[0], -1])
        # 2D Tensor of size [batch_size x nwords]
        out = self.fnn(emb_view)
        return out

In [5]:
# Initialize the model and the optimizer
model = FFN_LM(nwords=nwords, emb_size=EMB_SIZE, hid_size=HID_SIZE, num_hist=N, dropout=0.2)

In [6]:
optimizer = tf.keras.optimizers.Adam()
loss_fn = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)

In [7]:
def convert_to_variables(words):
    var = tf.constant(words)
    return var

In [8]:
# A function to calculate scores for one value
def calc_score_of_histories(words):
    # This will change from a list of histories, to a pytorch Variable whose data type is LongTensor
    words_var = convert_to_variables(words)
    logits = model(words_var)
    return logits

In [9]:
@tf.function(experimental_relax_shapes=True)
def step(words_var, all_targets):
    with tf.GradientTape() as tape:
        logits = model(words_var)
        loss = loss_fn(all_targets, logits)
    grads = tape.gradient(loss, model.trainable_variables)
    optimizer.apply_gradients(zip(grads, model.trainable_variables))
    return loss


@tf.function(experimental_relax_shapes=True)
def valid_step(words_var, all_targets):
    logits = model(words_var)
    loss = loss_fn(all_targets, logits)
    return loss

In [10]:
# Calculate the loss value for the entire sentence
def calc_sent_loss(sent):
    # The initial history is equal to end of sentence symbols
    hist = [S] * N
    # Step through the sentence, including the end of sentence token
    all_histories = []
    all_targets = []
    for next_word in sent + [S]:
        all_histories.append(list(hist))
        all_targets.append(next_word)
        hist = hist[1:] + [next_word]
    words_var = convert_to_variables(all_histories)
    all_targets = convert_to_variables(all_targets)
    loss = step(words_var, all_targets)
    return loss

In [11]:
# Calculate the loss value for the entire sentence
def calc_valid_sent_loss(sent):
    # The initial history is equal to end of sentence symbols
    hist = [S] * N
    # Step through the sentence, including the end of sentence token
    all_histories = []
    all_targets = []
    for next_word in sent + [S]:
        all_histories.append(list(hist))
        all_targets.append(next_word)
        hist = hist[1:] + [next_word]
    words_var = convert_to_variables(all_histories)
    all_targets = convert_to_variables(all_targets)
    loss = valid_step(words_var, all_targets)
    return loss

In [14]:
MAX_LEN = 2
# Generate a sentence
def generate_sent():
    hist = [S] * N
    sent = []
    while True:
        logits = calc_score_of_histories([hist])
        prob = tf.keras.activations.softmax(logits)
        print(prob)
#         print(sampled_indices)
#         next_word = prob.multinomial().data[0,0]
        if len(sent) == MAX_LEN:
            break
        sent.append(1)
#         hist = hist[1:] + [next_word]
#     return sent

In [ ]:
last_dev = 1e20
best_dev = 1e20
for ITER in range(5):
    # Perform training
    random.shuffle(train)
    # set the model to training mode
    train_words, train_loss = 0, 0.0
    start = time.time()
    for sent_id, sent in enumerate(train[:2]):
        my_loss = calc_sent_loss(sent)
        train_loss += my_loss.numpy()
        print("train_loss: {}".format(train_loss))
        train_words += len(sent)
        if (sent_id+1) % 5000 == 0:
            print("--finished %r sentences (word/sec=%.2f)" % (sent_id+1, train_words/(time.time()-start)))
    print("iter %r: train loss/word=%.4f, ppl=%.4f (word/sec=%.2f)" % (ITER, train_loss/train_words, math.exp(train_loss/train_words), train_words/(time.time()-start)))
  
     # Evaluate on dev set
#     # set the model to evaluation mode
#     model.eval()
    dev_words, dev_loss = 0, 0.0
    start = time.time()
    for sent_id, sent in enumerate(dev[:2]):
        my_loss = calc_valid_sent_loss(sent)
        dev_loss += my_loss.numpy()
        dev_words += len(sent)

# Keep track of the development accuracy and reduce the learning rate if it got worse
    if last_dev < dev_loss:
        print("Optimizer lr --->")
        print(optimizer._decayed_lr)
    last_dev = dev_loss

# Keep track of the best development accuracy, and save the model only if it's the best one
#     if best_dev > dev_loss:
#         model.save('saved_lm_model.h5', overwrite=True)
#         best_dev = dev_loss
  
  # Save the model
    print("iter %r: dev loss/word=%.4f, ppl=%.4f (word/sec=%.2f)" % (ITER, dev_loss/dev_words, math.exp(dev_loss/dev_words), dev_words/(time.time()-start)))
  #Generate a few sentences
    for _ in range(5):
        generate_sent()
#         print(" ".join([i2w[x] for x in sent]))

train_loss: 9.211738586425781
train_loss: 18.421695709228516
iter 0: train loss/word=0.2924, ppl=1.3396 (word/sec=55.37)
iter 0: dev loss/word=0.4492, ppl=1.5670 (word/sec=215.94)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), d

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

...

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 

tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 9.9484794e-05 9.9291945e-05 ... 9.9607059e-05
  1.0022426e-04 9.9973069e-05]], shape=(1, 10000), dtype=float32)
tf.Tensor(
[[1.0017045e-04 